In [29]:
from sentence_transformers import SentenceTransformer
from bertopic import BERTopic
from openai import OpenAI
from umap import UMAP
import pandas as pd
import sys

In [6]:
# Add the scripts directory to the path
sys.path.append('../scripts')
# Own scripts
import pubmed_helpers
import text_cleaning as tc

In [2]:
df = pd.read_parquet('data/pubmed_data_200.parquet')

In [7]:
# Clean the text with Spacy
cleaned_docs = [tc.clean_text_ext_spacy(doc) for doc in df['abstract']]

In [8]:
# Add the cleaned text back in the dataframe
df['cleaned_abstract'] = cleaned_docs

In [12]:
df_applications = pd.read_excel('../data/test_records.xlsx', engine='calamine')

In [15]:
df_applications.columns

Index(['application_reference', 'project_title', 'is_grant', 'is_application',
       'call_name', 'granted_amount', 'brief_project_description',
       'project_description'],
      dtype='object')

In [16]:
cleaned_application_project_description = [tc.clean_text_ext_spacy(doc) for doc in df_applications['project_description']]

In [17]:
cleaned_application_brief_project_description = [tc.clean_text_ext_spacy(doc) for doc in df_applications['brief_project_description']]

In [23]:
df_applications['cleaned_project_description'] = cleaned_application_project_description
df_applications['cleaned_brief_project_description'] = cleaned_application_brief_project_description

In [24]:
# Write df_applications to parquet
df_applications.to_parquet('../data/test_records_cleaned.parquet')

In [43]:
sentence_model = SentenceTransformer('sentence-transformers/allenai-specter')

embeddings = sentence_model.encode(df_applications['cleaned_project_description'], show_progress_bar=True)

topic_model = BERTopic().fit(df_applications['cleaned_project_description'], embeddings)

Batches:   0%|          | 0/11 [00:00<?, ?it/s]

In [44]:
topic_model.visualize_barchart()

In [45]:
def get_topic_representation(keywords, ollama_model="llama3.2:1b"):
    client = OpenAI(
        api_key='ollama',  
        # api_version = "2024-02-15-preview",
        base_url='http://localhost:11434/v1/',
    )
    # Create the prompt to generate a concise topic label
    prompt = f"Here is a list of keywords that represent a topic: {', '.join(keywords)}. Can you generate a concise and meaningful topic label for this? Please respond only with the topic label."

    # Generate the topic label using the GPT-4 model
    response = client.chat.completions.create(
            # model = "gpt4-nnfimpact",
            model = ollama_model,
            temperature = 0.0,
            messages = [
                    {"role": "user", "content": prompt}
            ]
        )
    return response.choices[0].message.content

In [46]:
def get_topic_labels():
    """Call the get_topic_representation function for each topic in the topic model."""
    topic_label = []
    for topic in topic_model.get_topic_info()['Representation']:
        topic_label.append(get_topic_representation(topic))
    return topic_label

In [155]:
# Use the Ollama local model to generate topic labels
topic_labels = get_topic_labels()

In [156]:
# Set the topic labels in the topic model
topic_model.set_topic_labels(topic_labels)

In [157]:
df_applications['application_reference'] = df_applications['application_reference'].astype(str)

In [55]:
# Run the visualization with the original embeddings
topic_model.visualize_documents(df_applications['application_reference'], embeddings=embeddings, custom_labels=True, )

In [39]:

reduced_embeddings = UMAP(n_neighbors=10, n_components=2, min_dist=0.0, metric='cosine').fit_transform(embeddings)
topic_model.visualize_documents(df_applications['cleaned_project_description'], reduced_embeddings=reduced_embeddings, custom_labels=True)

In [57]:
df_applications_large = pd.read_excel('../data/endocrinology_metabolism_2020_to_2024_and_bbm_project_grants_2018_to_2024.xlsx', engine='calamine')

In [59]:
cleaned_application_project_description = [tc.clean_text_ext_spacy(doc) for doc in df_applications_large['project_description']]
cleaned_application_brief_project_description = [tc.clean_text_ext_spacy(doc) for doc in df_applications_large['brief_project_description']]
df_applications_large['cleaned_project_description'] = cleaned_application_project_description
df_applications_large['cleaned_brief_project_description'] = cleaned_application_brief_project_description
df_applications_large.to_parquet('../data/endocrinology_metabolism_2020_to_2024_and_bbm_project_grants_2018_to_2024.parquet')
sentence_model = SentenceTransformer('sentence-transformers/allenai-specter')
embeddings = sentence_model.encode(df_applications_large['cleaned_project_description'], show_progress_bar=True)
topic_model = BERTopic().fit(df_applications_large['cleaned_project_description'], embeddings)
# Use the Ollama local model to generate topic labels
topic_labels = get_topic_labels()

Batches:   0%|          | 0/73 [00:00<?, ?it/s]

In [154]:
topic_model.set_topic_labels(topic_labels)

ValueError: Make sure that `topic_labels` contains the same number of labels as there are topics.

In [115]:
topics, probs = topic_model.fit_transform(df_applications_large['cleaned_project_description'])

In [116]:
new_topics = topic_model.reduce_outliers(df_applications_large['cleaned_project_description'], topics)
topic_model_smaller = topic_model
topic_model_smaller.update_topics(df_applications_large['cleaned_project_description'], topics=new_topics)
topic_model_smaller.get_topic_info()

2025-01-21 21:11:25,171 - BERTopic - WARNING: Using a custom list of topic assignments may lead to errors if topic reduction techniques are used afterwards. Make sure that manually assigning topics is the last step in the pipeline.Note that topic embeddings will also be created through weightedc-TF-IDF embeddings instead of centroid embeddings.


Topic  Count                                            Name  \
0       0    174                       0_islet_cell_insulin_beta   
1       1    106           1_antibiotic_infection_phage_bacteria   
2       2    180                2_protein_structure_peptide_bind   
3       3     98              3_muscle_exercise_skeletal_glucose   
4       4     85                      4_liver_nafld_nash_hepatic   
5       5     79                      5_heart_cardiac_af_channel   
6       6     74                   6_pcos_follicle_woman_ovarian   
7       7     62           7_bone_fracture_osteoporosis_estrogen   
8       8     62             8_ldl_cholesterol_lipoprotein_lipid   
9       9     98                 9_risk_diabetes_genetic_patient   
10     10     69                           10_pd_ad_brain_neuron   
11     11     69               11_adipocyte_adipose_tissue_lipid   
12     12     65                       12_kidney_renal_ckd_mouse   
13     13     82                     13_cancer_tumor_cell_breast   
14     14     53                    14_virus_viral_infection_rna   
15     15     66                  15_food_intake_appetite_neuron   
16     16     42                    16_pregnancy_gdm_fetal_birth   
17     17     57                17_intestinal_gut_ibd_microbiome   
18     18     51                      18_gut_microbiota_diet_imp   
19     19     43                19_dna_replication_damage_repair   
20     20     49                   20_tumor_cancer_cell_melanoma   
21     21     50                      21_cell_antigen_immune_ige   
22     22     33               22_senescence_senescent_aging_age   
23     23     59                 23_insulin_glucose_mouse_tissue   
24     24     42              24_stroke_microglia_brain_recovery   
25     25     29            25_thyroid_gd_hypothyroidism_patient   
26     26     32                  26_bat_brown_adipocyte_adipose   
27     27     36  27_mitochondrial_mitochondria_mtdna_metabolism   
28     28     50                        28_rna_protein_mrna_bind   
29     29     47             29_neuron_neuronal_synaptic_circuit   
30     30     34               30_histone_chromatin_enhancer_dna   
31     31     26            31_malaria_antibody_parasite_vaccine   
32     32     28                       32_bmi_obesity_child_risk   
33     33     39               33_brain_neuron_astrocyte_insulin   
34     34     22        34_hypertension_vascular_artery_pressure   
35     35     20          35_patient_autoimmune_autoantibody_aad   
36     36     21               36_crispr_editing_endosome_target   
37     37     14                      37_csf_ncbe_choroid_plexus   
38     38     13                            38_te_ecm_fn_oxidant   
39     39     13                    39_hcv_vaccine_virus_epitope   
40     40     13                 40_circadian_sleep_rhythm_clock   
41     41     12               41_antidepressant_mental_nr_brain   
42     42     13                           42_hsc_stem_hscs_nend   
43     43     10          43_sperm_epigenetic_inheritance_sncrna   
44     44     12                       44_dl_surgery_obesity_pig   

                                       Representation  \
0   [islet, cell, insulin, beta, pancreatic, secre...   
1   [antibiotic, infection, phage, bacteria, bacte...   
2   [protein, structure, peptide, bind, drug, comp...   
3   [muscle, exercise, skeletal, glucose, insulin,...   
4   [liver, nafld, nash, hepatic, hepatocyte, fibr...   
5   [heart, cardiac, af, channel, cam, cardiomyocy...   
6   [pcos, follicle, woman, ovarian, sex, hormone,...   
7   [bone, fracture, osteoporosis, estrogen, osteo...   
8   [ldl, cholesterol, lipoprotein, lipid, aaa, hd...   
9   [risk, diabetes, genetic, patient, disease, da...   
10  [pd, ad, brain, neuron, disease, protein, aggr...   
11  [adipocyte, adipose, tissue, lipid, obesity, m...   
12  [kidney, renal, ckd, mouse, ncc, urine, megali...   
13  [cancer, tumor, cell, breast, repair, aml, pat...   
14  [virus, viral, i

In [114]:
topic_model.save('../data/endocrinology_metabolism_2020_to_2024_and_bbm_project_grants_2018_to_2024_model.safetensors', serialization='safetensors')

In [122]:
load_bertopic = BERTopic.load('../data/endocrinology_metabolism_2020_to_2024_and_bbm_project_grants_2018_to_2024_model.safetensors')


2025-01-21 21:15:39,122 - BERTopic - WARNING: You are loading a BERTopic model without explicitly defining an embedding model. If you want to also load in an embedding model, make sure to use `BERTopic.load(my_model, embedding_model=my_embedding_model)`.


In [64]:
# topic_model.save('../data/endocrinology_metabolism_2020_to_2024_and_bbm_project_grants_2018_to_2024_model.safetensors', serialization='safetensors')

In [ ]:
# new_topics = topic_model.reduce_outliers(cleaned_docs, topics)
# topic_model.update_topics(cleaned_docs, topics=new_topics)
# topic_model.get_topic_info()

In [70]:
df_applications_large.columns

Index(['application_reference', 'project_title', 'is_grant', 'is_application',
       'call_name', 'granted_amount', 'brief_project_description',
       'project_description', 'time_dimension_date',
       'cleaned_project_description', 'cleaned_brief_project_description'],
      dtype='object')

In [72]:
# topic_model.visualize_topics_over_time(df_applications_large['time_dimension_date'])

topics_over_time = topic_model.topics_over_time(df_applications_large['cleaned_project_description'], df_applications_large['time_dimension_date'], nr_bins=20)

In [125]:
load_bertopic.visualize_topics_over_time(topics_over_time, custom_labels=True, topics=range(10))

In [129]:
df_applications_large.columns

Index(['application_reference', 'project_title', 'is_grant', 'is_application',
       'call_name', 'granted_amount', 'brief_project_description',
       'project_description', 'time_dimension_date',
       'cleaned_project_description', 'cleaned_brief_project_description'],
      dtype='object')

In [131]:
with_topics = load_bertopic.get_document_info(df_applications_large['application_reference'].astype(str))

In [136]:
with_topics = with_topics.rename(columns={'Document': 'application_reference'})

In [138]:
df_applications_large['application_reference'] = df_applications_large['application_reference'].astype(str)

In [140]:
result = with_topics.merge(df_applications_large, on='application_reference')

In [142]:
result.to_parquet('../data/endocrinology_metabolism_2020_to_2024_and_bbm_project_grants_2018_to_2024_with_topics.parquet')

In [147]:
result[['application_reference','CustomName', 'is_grant', 'time_dimension_date', 'granted_amount', 'call_name']].to_clipboard(index=False)

In [152]:
topic_model.get_topic_info()

Topic  Count                                            Name  \
0       0    174                       0_islet_cell_insulin_beta   
1       1    106           1_antibiotic_infection_phage_bacteria   
2       2    180                2_protein_structure_peptide_bind   
3       3     98              3_muscle_exercise_skeletal_glucose   
4       4     85                      4_liver_nafld_nash_hepatic   
5       5     79                      5_heart_cardiac_af_channel   
6       6     74                   6_pcos_follicle_woman_ovarian   
7       7     62           7_bone_fracture_osteoporosis_estrogen   
8       8     62             8_ldl_cholesterol_lipoprotein_lipid   
9       9     98                 9_risk_diabetes_genetic_patient   
10     10     69                           10_pd_ad_brain_neuron   
11     11     69               11_adipocyte_adipose_tissue_lipid   
12     12     65                       12_kidney_renal_ckd_mouse   
13     13     82                     13_cancer_tumor_cell_breast   
14     14     53                    14_virus_viral_infection_rna   
15     15     66                  15_food_intake_appetite_neuron   
16     16     42                    16_pregnancy_gdm_fetal_birth   
17     17     57                17_intestinal_gut_ibd_microbiome   
18     18     51                      18_gut_microbiota_diet_imp   
19     19     43                19_dna_replication_damage_repair   
20     20     49                   20_tumor_cancer_cell_melanoma   
21     21     50                      21_cell_antigen_immune_ige   
22     22     33               22_senescence_senescent_aging_age   
23     23     59                 23_insulin_glucose_mouse_tissue   
24     24     42              24_stroke_microglia_brain_recovery   
25     25     29            25_thyroid_gd_hypothyroidism_patient   
26     26     32                  26_bat_brown_adipocyte_adipose   
27     27     36  27_mitochondrial_mitochondria_mtdna_metabolism   
28     28     50                        28_rna_protein_mrna_bind   
29     29     47             29_neuron_neuronal_synaptic_circuit   
30     30     34               30_histone_chromatin_enhancer_dna   
31     31     26            31_malaria_antibody_parasite_vaccine   
32     32     28                       32_bmi_obesity_child_risk   
33     33     39               33_brain_neuron_astrocyte_insulin   
34     34     22        34_hypertension_vascular_artery_pressure   
35     35     20          35_patient_autoimmune_autoantibody_aad   
36     36     21               36_crispr_editing_endosome_target   
37     37     14                      37_csf_ncbe_choroid_plexus   
38     38     13                            38_te_ecm_fn_oxidant   
39     39     13                    39_hcv_vaccine_virus_epitope   
40     40     13                 40_circadian_sleep_rhythm_clock   
41     41     12               41_antidepressant_mental_nr_brain   
42     42     13                           42_hsc_stem_hscs_nend   
43     43     10          43_sperm_epigenetic_inheritance_sncrna   
44     44     12                       44_dl_surgery_obesity_pig   

                                       Representation  \
0   [islet, cell, insulin, beta, pancreatic, secre...   
1   [antibiotic, infection, phage, bacteria, bacte...   
2   [protein, structure, peptide, bind, drug, comp...   
3   [muscle, exercise, skeletal, glucose, insulin,...   
4   [liver, nafld, nash, hepatic, hepatocyte, fibr...   
5   [heart, cardiac, af, channel, cam, cardiomyocy...   
6   [pcos, follicle, woman, ovarian, sex, hormone,...   
7   [bone, fracture, osteoporosis, estrogen, osteo...   
8   [ldl, cholesterol, lipoprotein, lipid, aaa, hd...   
9   [risk, diabetes, genetic, patient, disease, da...   
10  [pd, ad, brain, neuron, disease, protein, aggr...   
11  [adipocyte, adipose, tissue, lipid, obesity, m...   
12  [kidney, renal, ckd, mouse, ncc, urine, megali...   
13  [cancer, tumor, cell, breast, repair, aml, pat...   
14  [virus, viral, i

In [84]:
topics_over_time.columns

Index(['Topic', 'Words', 'Frequency', 'Timestamp', 'Name'], dtype='object')

In [86]:
topics_over_time['Year'] = topics_over_time['Timestamp'].dt.year


In [106]:
# Frequency of topics over time
topics_over_time[['Year', 'Name', 'Frequency',]].to_clipboard(index=False)

In [101]:
topics_over_time.groupby(['Year', "Name"]).size().unstack(fill_value=0)

Topic                                         Words  Frequency  \
0       -1             cell, protein, project, gene, dna         56   
1        0         cell, proinsulin, insulin, crs, islet          5   
2        1  muscle, exercise, skeletal, tendon, training          6   
3        2  antibiotic, biofilm, phage, bacteria, strain         14   
4        3              liver, nafld, nash, hcc, hepatic          6   
..     ...                                           ...        ...   
319     37              sortilin, cnv, rpe, retinal, amd          1   
320     38     sleep, circadian, hcrt, melatonin, rhythm          4   
321     39               club, lung, airway, dirty, cell          2   
322     40       motor, neuron, striatal, error, sensory          2   
323     41    lps, minute, maj, inflammation, calcitonin          1   

                  Timestamp  \
0   2018-12-28 19:45:07.200   
1   2018-12-28 19:45:07.200   
2   2018-12-28 19:45:07.200   
3   2018-12-28 19:45:07.200   
4   2018-12-28 19:45:07.200   
..                      ...   
319 2024-08-29 03:36:00.000   
320 2024-08-29 03:36:00.000   
321 2024-08-29 03:36:00.000   
322 2024-08-29 03:36:00.000   
323 2024-08-29 03:36:00.000   

                                                  Name  Year  
0    Cellular Disease Study Analysis Proteomics Res...  2018  
1             Islet Cell Function in Diabetes Research  2018  
2    Muscle Training and Nutrition for Optimal Heal...  2018  
3    Antimicrobial Resistance in Bacterial Infectio...  2018  
4                Liver Disease and Metabolic Disorders  2018  
..                                                 ...   ...  
319     Retinal Cell Signaling Pathways in AMD and CNV  2024  
320             Sleep Regulation and Circadian Rhythms  2024  
321      Respiratory Cell Biology and Disease Research  2024  
322  Neurological Circuitry in Motor Control and Ne...  2024  
323  Biological Mechanisms in Obesity and Metabolic...  2024  

[324 rows x 6 columns]

In [100]:
palette = "viridis"
df_topics = topics_over_time.groupby(['Year', "Name"]).size().unstack(fill_value=0)

df_topics.to_clipboard()#.plot(kind='bar', stacked=True, colormap=palette)
# topics_over_time.plot(kind='bar', stacked=True, figsize=(10, 6), colormap=palette)

In [162]:
with_topics

application_reference  Topic                                Name  \
0                    51994      7               7_obesity_imp_fat_gut   
1                    52000     13        13_pd_ad_protein_aggregation   
2                    52001     -1       -1_cell_project_protein_datum   
3                    52003     31                   31_te_ecm_fn_cell   
4                    52004     29  29_synaptic_protein_mutation_brain   
...                    ...    ...                                 ...   
2327                 96466     10  10_adipocyte_adipose_insulin_lipid   
2328                 96470     -1       -1_cell_project_protein_datum   
2329                 96480      9     9_cell_antigen_immune_chemokine   
2330                 96490     30         30_skin_melanoma_tumor_cell   
2331                 96491     12          12_hcv_virus_viral_vaccine   

                                             CustomName  \
0     Nutritional Risk Factors for Obesity and Relat...   
1     Neurodegenerative Disease Research on Protein ...   
2     Cellular Disease Study Analysis Proteomics Res...   
3                    Cell Differentiation and Oxidation   
4     Neurotransmitter Regulation in Organoids and B...   
...                                                 ...   
2327  Metabolic Regulation in Obesity and Adiposity ...   
2328  Cellular Disease Study Analysis Proteomics Res...   
2329  Cellular Immune Response to Antigens and Chemo...   
2330           Molecular Pathways in Cutaneous Melanoma   
2331  Viral Infections and Vaccines Against HCV and ...   

                                         Representation  Representative_Docs  \
0     [obesity, imp, fat, gut, microbiota, diet, ris...                  NaN   
1     [pd, ad, protein, aggregation, neuron, disease...                  NaN   
2     [cell, project, protein, datum, study, mouse, ...                  NaN   
3     [te, ecm, fn, cell, nend, ipscs, differentiati...                  NaN   
4     [synaptic, protein, mutation, brain, adnp, neu...                  NaN   
...                                                 ...                  ...   
2327  [adipocyte, adipose, insulin, lipid, obesity, ...                  NaN   
2328  [cell, project, protein, datum, study, mouse, ...                  NaN   
2329  [cell, antigen, immune, chemokine, tcr, ms, es...                  NaN   
2330  [skin, melanoma, tumor, cell, lv, psoriasis, s...                  NaN   
2331  [hcv, virus, viral, vaccine, infection, protei...                  NaN   

                                            Top_n_words  \
0     obesity - imp - fat - gut - microbiota - diet ...   
1     pd - ad - protein - aggregation - neuron - dis...   
2     cell - project - protein - datum - study - mou...   
3     te - ecm - fn - cell - nend - ipscs - differen...   
4     synaptic - protein - mutation - brain - adnp -...   
...                                                 ...   
2327  adipocyte - adipose - insulin - lipid - obesit...   
2328  cell - project - protein - datum - study - mou...   
2329  cell - antigen - immune - chemokine - tcr - ms...   
2330  skin - melanoma - tumor - cell - lv - psoriasi...   
2331  hcv - virus - viral - vaccine - infection - pr...   

      Representative_document  
0                       False  
1                       False  
2                       False  
3                       False  
4                       False  
...                       ...  
2327                    False  
2328                    False  
2329                    False  
2330                    False  
2331                    False  

[2332 rows x 8 columns]

In [170]:
result.columns

Index(['application_reference', 'Topic', 'Name', 'CustomName',
       'Representation', 'Representative_Docs', 'Top_n_words',
       'Representative_document', 'project_title', 'is_grant',
       'is_application', 'call_name', 'granted_amount',
       'brief_project_description', 'project_description',
       'time_dimension_date', 'cleaned_project_description',
       'cleaned_brief_project_description'],
      dtype='object')

In [176]:
# Concate application_reference, project_title and CustomName for the visualization
result['cluster_title'] = result['application_reference']  + ' - ' + result['project_title'] + ' - ' + result['CustomName']

In [177]:
topic_model.visualize_documents(result['cluster_title'], custom_labels=True, hide_annotations=True, width=2000, height=1000)

In [178]:
fig = topic_model.visualize_documents(result['cluster_title'], custom_labels=True, hide_annotations=True, width=2000, height=1000)

In [179]:
fig.write_html('../data/demo.html')